# Obtaining the Dataset


(no ML in this entire section)

### Spotify API

In [2]:
import json
import requests
import base64

client id and secret are unique to registered Spotify web app, code is temporary and retrieved from separate Flask app

In [1]:
client_id = '30daab6eacde4b04901c9c6929ed49ea'
client_secret = 'cac7e435e9ca4af39aa9e9bd48beae1d'
code = 'AQA3Mg1Ujlbfa7PXn8DiC4PI0Wossa06dHj4eNsT60pwp01A0U0OjyAfZJW-oFixpyMRUr4oILsws2ozhabJBekZG0RdAMO8UjmVU9nqNHF3Yl-wwpHRNAf0rtG_6oH1gc7IbumDBru9CboDfEtB71gEhElzYmMrieqZ8J3MwrvjbBl-zzL8O_U3U4ZAJ3A_Y2V3K6Xztil3c_Zel2J1ncglm5oz6caGUCRYWc7qWKSrR7VLrkcXisJ68C4J6w'

In [6]:
# # NOTE: THESE ARE FOR USER DATA, NOT GENERAL SEARCH
# auth_header = base64.urlsafe_b64encode(f'{client_id}:{client_secret}'.encode('ascii'))
# token_url = "https://accounts.spotify.com/api/token"
# token_data = {
#     'grant_type':'authorization_code',
#     'code': code,
#     'redirect_uri': 'http://127.0.0.1:5000/' # running the get_code.py program locally
# }
# token_headers = {
#     # "Authorization": f"Basic {encoded_client_creds}"
#     'Authorization': f'Basic {auth_header.decode("ascii")}' # or just encoded_client_creds here
# }
# r = requests.post(token_url, data=token_data, headers=token_headers)
# print(r.json()) # not needed until retrieving from user data
# token_response_data = r.json()

Retrieve songs and lyrics

In [8]:
auth_header = base64.urlsafe_b64encode(f'{client_id}:{client_secret}'.encode('ascii'))
token_url = "https://accounts.spotify.com/api/token"
token_data = {
    'grant_type':'client_credentials',
    'code': code,
    'redirect_uri': 'http://127.0.0.1:5000/' # running the get_code.py program locally
}
token_headers = {
    # "Authorization": f"Basic {encoded_client_creds}"
    'Authorization': f'Basic {auth_header.decode("ascii")}' # or just encoded_client_creds here
}

In [9]:
r = requests.post(token_url, data=token_data, headers=token_headers)
print(r.json()) # note: diff from user api functions; only searches publically available data
token_response_data = r.json()

{'access_token': 'BQCoULPu03IFQU_yuqa1fZO0D3xvadDEX29gzZ3oZhvf5AHnqmBne8tEif1NYrhgIIesuvrolXgGNWnVqp7LV4vOMp_rAvcmFlVjNzXWWqERGI1-BkM', 'token_type': 'Bearer', 'expires_in': 3600}


In [25]:
print(r.json()['access_token'])

BQCoULPu03IFQU_yuqa1fZO0D3xvadDEX29gzZ3oZhvf5AHnqmBne8tEif1NYrhgIIesuvrolXgGNWnVqp7LV4vOMp_rAvcmFlVjNzXWWqERGI1-BkM


In [26]:
# Green Day, The Strokes, The Velvet Underground, Slaughter Beach, Dog, Fleetwood Mac, Mitski, and boygenius
# 0          1            2                       3                     4              5           6

# got these manually from artist's IDs in their share links
artist_ids = ['7oPftvlwr6VrsViSDV7fJY', '0epOFNiUfyON9EYx7Tpr6V', '1nJvji2KIlWSseXRSlNYsC', '3lWVgSwutPsiJ8Awm7OTKU', '08GQAI4eElDnROBrJRGE0X', '2uYWxilOVlUdk4oV9DvwqK', '1hLiboQ98IQWhpKeP9vRFw']
headers = {
    'Authorization': f"Bearer {token_response_data['access_token']}",
    'Content-Type': 'application/json'
}

In [27]:
# loop through artists to retrieve albums
responses=[]
for id in artist_ids:
  responses.append(requests.get(f"https://api.spotify.com/v1/artists/{id}/albums", headers=headers).json())

In [61]:
# responses # full api response

In [30]:
responses[0]['items'][0]['id']

'47l8TkJCLzHaekHImz1e9g'

Each entry in `responses` is a response containing all of artist `i`'s albums. Loop through `responses` and replace the response by a list of album Spotify IDs

In [33]:
album_ids = []
for i in range(len(responses)):
  album_list = []
  print("len(responses[i]['items']):", len(responses[i]['items']))
  for j in range(len(responses[i]['items'])):
    album_list.append(responses[i]['items'][j]['id'])
  album_ids.append(album_list)

len(responses[i]['items']): 20
len(responses[i]['items']): 20
len(responses[i]['items']): 20
len(responses[i]['items']): 20
len(responses[i]['items']): 20
len(responses[i]['items']): 16
len(responses[i]['items']): 20


In [60]:
# album_ids # list of list of green day album ids

Retrieve all track IDs for each album

In [34]:
track_ids = []
for artist_discog in album_ids: # there are 7 artist_discogs, each being a list
  tracks = []
  for album_id in artist_discog:
    tracks.append(requests.get(f"https://api.spotify.com/v1/albums/{album_id}/tracks", headers=headers).json())
  track_ids.append(tracks)

In [70]:
# 3rd artist tracks, 1st album, 1st song id
track_ids[2][0]['items'][0]['id']

'3SFayZBTps4PWfSIc8Pil5'

Compile all track ID's into a single list for each artist

In [47]:
bare_track_ids = []
for i in range(len(track_ids)): # loop through artists
  ids = []
  for j in range(len(track_ids[i])): # loop through albums
    for k in range(len(track_ids[i][j]['items'])):
      ids.append(track_ids[i][j]['items'][k]['id'])
  bare_track_ids.append(ids)

In [62]:
# bare_track_ids[0] # list of green day song ids

In [54]:
# print num songs for each artist
for artist in bare_track_ids:
  print(len(artist))

296
157
254
173
335
153
343


### Lyric API

Isolate words from API response

In [71]:
lyricurl = 'https://spotify-lyric-api-984e7b4face0.herokuapp.com/?trackid=6PmbpHTKSmKP3FuMIbjttI' #sub
lyric_data = {
    "trackid": '6PmbpHTKSmKP3FuMIbjttI' #sub
}
lyric_response = requests.get(lyricurl, data=lyric_data)
lyric_response.json()

{'error': False,
 'syncType': 'LINE_SYNCED',
 'lines': [{'startTimeMs': '12150',
   'words': "Where's the harm in voicing a doubt?",
   'syllables': [],
   'endTimeMs': '0'},
  {'startTimeMs': '17160',
   'words': "You'll find me in the lavatory",
   'syllables': [],
   'endTimeMs': '0'},
  {'startTimeMs': '21120',
   'words': "And where's the harm in talking out loud",
   'syllables': [],
   'endTimeMs': '0'},
  {'startTimeMs': '26190',
   'words': "When I'm on my own?",
   'syllables': [],
   'endTimeMs': '0'},
  {'startTimeMs': '31130',
   'words': "What's so wrong with reading my stars",
   'syllables': [],
   'endTimeMs': '0'},
  {'startTimeMs': '36150',
   'words': "When I'll be in the lavatory?",
   'syllables': [],
   'endTimeMs': '0'},
  {'startTimeMs': '40140',
   'words': 'And what is so wrong with counting the cars',
   'syllables': [],
   'endTimeMs': '0'},
  {'startTimeMs': '46280',
   'words': "When I'm all alone?",
   'syllables': [],
   'endTimeMs': '0'},
  {'startTime

In [80]:
words = ""
for line in lyric_response.json()['lines']:
  if (line['words'] != '♪') or (line['words'] != ''):
    words+=line['words'] + " / "

In [81]:
words

"Where's the harm in voicing a doubt? / You'll find me in the lavatory / And where's the harm in talking out loud / When I'm on my own? / What's so wrong with reading my stars / When I'll be in the lavatory? / And what is so wrong with counting the cars / When I'm all alone? / You're not the only one that I know / And I'm too proud to talk to you anyway / You're not the only one that I know / And I'm far too proud to talk to you any day / So, I say I'm in love with the world / And what is so wrong with voicing a doubt / When I'm on my own? / It's perfectly fine to sleep in a chair / From Monday 'til Saturday / And what is so wrong with talking out loud / When I'm all alone? / You're not the only one that I know / And I'm too proud to talk to you anyway / You're, you're not the only one that I know / But I'm far too proud to talk to you any day / So they rode out west to the seaside / And they gladly decided to stay / After two hours wandering outside / Ooh, the sea air drove them away,

# Formatting Input Data

In [82]:
import pandas as pd

In [90]:
df = pd.DataFrame(columns=['label','lyrics'])
df.head()

Empty DataFrame
Columns: [label, lyrics]
Index: []

In [87]:
for i in range(len(bare_track_ids)):
  for id in bare_track_ids[i]:
    lyric_response = requests.get(f"https://spotify-lyric-api-984e7b4face0.herokuapp.com/?trackid={id}", data={"trackid": f"{id}"})
    words = ""
    print(lyric_response.json())
    if not lyric_response.json()['error']:
      for line in lyric_response.json()['lines']:
        if (line['words'] != '♪') or (line['words'] != ''):
          words+=line['words'] + " / "
    df.loc[len(df.index)] = [i, words]

{'error': False, 'syncType': 'LINE_SYNCED', 'lines': [{'startTimeMs': '1440', 'words': "I declare I don't care no more", 'syllables': [], 'endTimeMs': '0'}, {'startTimeMs': '4200', 'words': "I'm burning up and out and growing bored", 'syllables': [], 'endTimeMs': '0'}, {'startTimeMs': '7360', 'words': 'In my smoked out boring room', 'syllables': [], 'endTimeMs': '0'}, {'startTimeMs': '11610', 'words': 'My hair is shagging in my eyes', 'syllables': [], 'endTimeMs': '0'}, {'startTimeMs': '14770', 'words': 'Dragging my feet to hit the street tonight', 'syllables': [], 'endTimeMs': '0'}, {'startTimeMs': '17730', 'words': 'Drive along these shit town lights', 'syllables': [], 'endTimeMs': '0'}, {'startTimeMs': '22880', 'words': "I'm not growing up, I'm just burning out", 'syllables': [], 'endTimeMs': '0'}, {'startTimeMs': '27310', 'words': 'And I stepped in line to walk amongst the dead', 'syllables': [], 'endTimeMs': '0'}, {'startTimeMs': '32440', 'words': 'Oh, apathy has rained on me', 's

In [89]:
len(df.index)

1789